In [1]:
%load_ext autoreload
%autoreload 2
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torch_geometric.datasets.qm9 import QM9
import torch_geometric.datasets.qm9 as qm9
from torch_geometric.data import DataLoader
import torch_geometric.nn as tgnn
from torch_geometric.data import Data
from torch_scatter import scatter
import torch_geometric
import tqdm
import numpy as np
import wandb
import random
import pandas as pd

import rdkit
from rdkit import Chem
from rdkit.Chem.rdchem import HybridizationType
from rdkit.Chem.rdchem import BondType as BT
from rdkit import RDLogger
RDLogger.DisableLog('rdApp.*')

import dfs_code
import _dfs_codes
import networkx as nx

manualSeed = 43
random.seed(manualSeed)
torch.manual_seed(manualSeed)
np.random.seed(manualSeed)
print("Random Seed: ", manualSeed)

Random Seed:  43


In [2]:
from torch_geometric.data import InMemoryDataset
class ChEMBL(InMemoryDataset):
    def __init__(self):
        super().__init__()
        self.data, self.slices = torch.load('../../datasets/ChEMBL/preprocessed.pt')

In [3]:
dataset = ChEMBL()

In [4]:
dfs_codes = {}
bad_examples = []
for data in tqdm.tqdm(dataset):
    vertex_features = data.x.detach().cpu().numpy()
    edge_features = data.edge_attr.detach().cpu().numpy()
    vertex_labels = np.argmax(vertex_features[:, :33], axis=1).tolist()
    edge_labels = np.argmax(edge_features, axis=1).tolist()
    if len(vertex_features) > 30:
        continue
    try:    
        code, dfs_indices = dfs_code.min_dfs_code_from_torch_geometric(data, vertex_labels, edge_labels)
        dfs_codes[data.name] = {'min_dfs_code':code, 'dfs_indices':dfs_indices}
    except KeyboardInterrupt:
        break
    except:
        print(data.name, 'failed')
        bad_examples += [data.name]
    """except KeyError as e:
        print('diagnosis: ')
        edges_coo = data.edge_index.detach().cpu().numpy().T
        edge2id = {tuple(e.tolist()): idx for idx, e in enumerate(edges_coo)}
        edge_list = dfs_code.torch_geometric_2_lists(data, vertex_labels, edge_labels)
        code = _dfs_codes.compute_minimal_dfs_code(edge_list, vertex_labels)
        dfs_indices = {}
        for idx, row in enumerate(code):
            code[idx][-2] = edge2id[(row[-3], row[-1])]
            dfs_indices[row[-3]] = row[0]
            dfs_indices[row[-1]] = row[1]
        g = nx.Graph()
        g.add_nodes_from(list(range(len(vertex_labels))))
        g.add_edges_from(edges_coo.tolist())
        print('has correct length?', len(code) == len(edge_list)//2,'is valid?', dfs_code.isValidDFSCode(code), end='')
        print(' is connected?', nx.is_connected(g))"""
    
        

  0%|                                                                                                                                                                      | 708/1914647 [00:00<08:31, 3739.64it/s]

CHEMBL2106510 failed
CHEMBL1402404 failed
CHEMBL1576274 failed
CHEMBL170462 failed
CHEMBL4060669 failed
CHEMBL3216898 failed
CHEMBL3188338 failed
CHEMBL1821783 failed
CHEMBL2107523 failed
CHEMBL3964957 failed
CHEMBL1203831 failed
CHEMBL1453498 failed
CHEMBL15228 failed
CHEMBL3344531 failed
CHEMBL545637 failed
CHEMBL103922 failed
CHEMBL170469 failed
CHEMBL29112 failed
CHEMBL1905014 failed
CHEMBL3498093 failed
CHEMBL1388136 failed
CHEMBL2106925 failed
CHEMBL3182439 failed


  0%|                                                                                                                                                                     | 1083/1914647 [00:00<12:34, 2536.50it/s]

CHEMBL1518709 failed
CHEMBL3426202 failed
CHEMBL1441419 failed
CHEMBL1301258 failed
CHEMBL92372 failed
CHEMBL2448034 failed
CHEMBL3504837 failed
CHEMBL4125688 failed
CHEMBL3207469 failed


  0%|▏                                                                                                                                                                    | 2016/1914647 [00:00<08:47, 3626.87it/s]

...

CHEMBL3416065 failed
CHEMBL2106085 failed
CHEMBL3330338 failed
CHEMBL4170396 failed
CHEMBL1200904 failed
CHEMBL4297676 failed
CHEMBL3289520 failed
CHEMBL4650309 failed
CHEMBL3498459 failed
CHEMBL4297319 failed
CHEMBL65375 failed
CHEMBL2106195 failed
CHEMBL4650347 failed
CHEMBL928 failed
CHEMBL1200841 failed
CHEMBL3208574 failed
CHEMBL3596561 failed
CHEMBL1200409 failed
CHEMBL1309811 failed
CHEMBL535362 failed
CHEMBL1200796 failed
CHEMBL2105613 failed
CHEMBL3501425 failed
CHEMBL3989844 failed
CHEMBL2021946 failed
CHEMBL3217024 failed
CHEMBL1461866 failed
CHEMBL1200434 failed
CHEMBL1097620 failed
CHEMBL3989406 failed
CHEMBL1964546 failed
CHEMBL3707387 failed
CHEMBL3989705 failed
CHEMBL1671 failed
CHEMBL555280 failed
CHEMBL296913 failed
CHEMBL567563 failed
CHEMBL64894 failed
CHEMBL4297472 failed
CHEMBL554222 failed
CHEMBL74939 failed
CHEMBL536471 failed
CHEMBL2107355 failed
CHEMBL4166653 failed
CHEMBL1256137 failed
CHEMBL3823277 failed
CHEMBL2237467 failed


100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▉| 1913749/1914647 [08:53<00:00, 2807.06it/s]

CHEMBL3501536 failed
CHEMBL1978502 failed
CHEMBL4650353 failed
CHEMBL1200964 failed
CHEMBL395017 failed
CHEMBL553664 failed
CHEMBL4129317 failed
CHEMBL1201020 failed
CHEMBL401698 failed
CHEMBL2024517 failed
CHEMBL462766 failed
CHEMBL536255 failed
CHEMBL1203661 failed
CHEMBL511347 failed
CHEMBL436020 failed
CHEMBL1200944 failed
CHEMBL1914661 failed
CHEMBL1881783 failed
CHEMBL558575 failed
CHEMBL1555 failed
CHEMBL2447974 failed
CHEMBL4297411 failed
CHEMBL1256175 failed
CHEMBL1200493 failed
CHEMBL1835351 failed
CHEMBL3989830 failed
CHEMBL1692 failed
CHEMBL3833336 failed
CHEMBL1889091 failed
CHEMBL4297365 failed
CHEMBL4297345 failed
CHEMBL1200381 failed
CHEMBL550755 failed
CHEMBL1377157 failed
CHEMBL1375743 failed
CHEMBL1201061 failed
CHEMBL1200804 failed
CHEMBL2068724 failed


100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1914647/1914647 [08:53<00:00, 3588.96it/s]

CHEMBL1200625 failed
CHEMBL1698 failed
CHEMBL1200750 failed
CHEMBL501 failed
CHEMBL2336050 failed
CHEMBL2105935 failed
CHEMBL1201728 failed
CHEMBL2107309 failed
CHEMBL738 failed
CHEMBL1701 failed
CHEMBL1201180 failed
CHEMBL1690 failed
CHEMBL1795071 failed
CHEMBL502109 failed
CHEMBL1709 failed
CHEMBL1200729 failed
CHEMBL2107546 failed
CHEMBL2364609 failed
CHEMBL1200735 failed
CHEMBL1905872 failed
CHEMBL535650 failed
CHEMBL3833347 failed
CHEMBL1200798 failed
CHEMBL1889140 failed
CHEMBL3707448 failed
CHEMBL4298043 failed
CHEMBL1201013 failed
CHEMBL4297221 failed
CHEMBL2106978 failed
CHEMBL1256472 failed
CHEMBL1256819 failed
CHEMBL1201777 failed
CHEMBL3181832 failed
CHEMBL1398126 failed
CHEMBL3184906 failed
CHEMBL2007389 failed
CHEMBL1200358 failed
CHEMBL904 failed
CHEMBL1200544 failed
CHEMBL1728 failed
CHEMBL2104496 failed
CHEMBL1200781 failed
CHEMBL4297204 failed
CHEMBL215645 failed
CHEMBL1003 failed
CHEMBL3544974 failed
CHEMBL1200758 failed
CHEMBL1201290 failed
CHEMBL1200778 failed
CHEM

In [5]:
len(bad_examples)

54809

In [7]:
len(dfs_codes)

1227962

In [8]:
bad_examples

['CHEMBL2106510',
 'CHEMBL1402404',
 'CHEMBL1576274',
 'CHEMBL170462',
 'CHEMBL4060669',
 'CHEMBL3216898',
 'CHEMBL3188338',
 'CHEMBL1821783',
 'CHEMBL2107523',
 'CHEMBL3964957',
 'CHEMBL1203831',
 'CHEMBL1453498',
 'CHEMBL15228',
 'CHEMBL3344531',
 'CHEMBL545637',
 'CHEMBL103922',
 'CHEMBL170469',
 'CHEMBL29112',
 'CHEMBL1905014',
 'CHEMBL3498093',
 'CHEMBL1388136',
 'CHEMBL2106925',
 'CHEMBL3182439',
 'CHEMBL1518709',
 'CHEMBL3426202',
 'CHEMBL1441419',
 'CHEMBL1301258',
 'CHEMBL92372',
 'CHEMBL2448034',
 'CHEMBL3504837',
 'CHEMBL4125688',
 'CHEMBL3207469',
 'CHEMBL2219741',
 'CHEMBL1319041',
 'CHEMBL604044',
 'CHEMBL41378',
 'CHEMBL3216649',
 'CHEMBL2105988',
 'CHEMBL535166',
 'CHEMBL1484056',
 'CHEMBL1546796',
 'CHEMBL3391915',
 'CHEMBL416830',
 'CHEMBL3500279',
 'CHEMBL1917705',
 'CHEMBL1782709',
 'CHEMBL3183084',
 'CHEMBL1526972',
 'CHEMBL4215209',
 'CHEMBL553323',
 'CHEMBL1173308',
 'CHEMBL1793902',
 'CHEMBL3819485',
 'CHEMBL1470193',
 'CHEMBL156986',
 'CHEMBL1571100',
 'CHEMBL1

In [10]:
!mkdir ../../datasets/ChEMBL/leq30

In [12]:
import json
with open('../../datasets/ChEMBL/leq30/bad_examples.json', 'w') as f:
    json.dump(bad_examples, f)

In [13]:
with open('../../datasets/ChEMBL/leq30/min_dfs_codes.json', 'w') as f:
    json.dump(dfs_codes, f)

In [14]:
dfs_codes

{'CHEMBL306107': {'min_dfs_code': [[0, 1, 0, 0, 0, 9, 19, 8],
   [1, 2, 0, 2, 0, 8, 16, 2],
   [2, 3, 0, 0, 1, 2, 3, 1],
   [3, 4, 1, 0, 0, 1, 1, 0],
   [2, 5, 0, 2, 0, 2, 4, 3],
   [5, 6, 0, 2, 0, 3, 7, 4],
   [6, 7, 0, 2, 0, 4, 9, 5],
   [7, 8, 0, 0, 3, 5, 11, 6],
   [7, 9, 0, 2, 0, 5, 12, 7],
   [9, 1, 0, 2, 0, 7, 15, 8],
   [0, 10, 0, 2, 0, 9, 20, 10],
   [10, 11, 0, 2, 0, 10, 23, 11],
   [11, 12, 0, 0, 2, 11, 25, 12],
   [12, 13, 2, 0, 0, 12, 28, 13],
   [13, 14, 0, 2, 0, 13, 30, 14],
   [14, 15, 0, 2, 0, 14, 33, 15],
   [15, 16, 0, 2, 0, 15, 35, 16],
   [16, 17, 0, 0, 3, 16, 37, 17],
   [16, 18, 0, 2, 0, 16, 38, 18],
   [18, 19, 0, 2, 0, 18, 41, 19],
   [19, 13, 0, 2, 0, 19, 42, 13],
   [11, 20, 0, 2, 2, 11, 26, 20],
   [20, 21, 2, 2, 0, 20, 45, 21],
   [21, 22, 0, 0, 2, 21, 47, 22],
   [21, 23, 0, 2, 2, 21, 48, 23],
   [23, 0, 2, 2, 0, 23, 50, 9]],
  'dfs_indices': [4,
   3,
   2,
   5,
   6,
   7,
   8,
   9,
   1,
   0,
   10,
   11,
   12,
   13,
   14,
   15,
   16,
   17,
 